## Importação de bibliotecas

In [1]:
import pandas as pd
import numpy as np

In [2]:
try:
    df = pd.read_csv('datasets/SIOE 2024-01-31.csv', encoding='latin-1', delimiter=';')
    print(df.info())
except pd.errors.ParserError as e:
    print("Error parsing CSV file:", e)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8797 entries, 0 to 8796
Data columns (total 49 columns):
 #   Column                                   Non-Null Count  Dtype 
---  ------                                   --------------  ----- 
 0   classe                                   8797 non-null   object
 1   tipo                                     8797 non-null   object
 2   código SIOE                              8797 non-null   int64 
 3   sigla                                    8797 non-null   object
 4   designação                               8797 non-null   object
 5   path                                     8797 non-null   object
 6   cae                                      8797 non-null   object
 7   sigla do ministério/secretaria regional  8797 non-null   object
 8   nome do ministério/secretaria regional   8797 non-null   object
 9   âmbito                                   8797 non-null   object
 10  endereço                                 8797 non-null   obj

In [9]:
#count the number of rows
print("Number of rows:", len(df))

#size grouped by distrito

print(df.groupby('distrito').size())
print("\n")
print(df.groupby('classe').size())
print("\n")
print(df.groupby('tipo').size())
print("\n")
print(df.groupby('cae').size())



Number of rows: 8797
distrito
 -                        3
Aveiro                  418
Beja                    230
Braga                   620
Bragança                364
Castelo Branco          275
Coimbra                 412
Faro                    300
Guarda                  384
Ilha Terceira           130
Ilha da Graciosa         23
Ilha da Madeira         343
Ilha das Flores          34
Ilha de Porto Santo      14
Ilha de Santa Maria      26
Ilha de São Jorge        37
Ilha de São Miguel      274
Ilha do Corvo            14
Ilha do Faial            68
Ilha do Pico             46
Leiria                  322
Lisboa                 1340
Portalegre              194
Porto                   803
Santarém                385
Setúbal                 327
Viana do Castelo        341
Vila Real               350
Viseu                   504
Évora                   216
dtype: int64


classe
Entidade        6199
Sub-Entidade    2598
dtype: int64


tipo
CN         750
CN+JUR    8047
dtype: int64


c

In [10]:
#save the data to a new file csv file iso-8859-1
df.to_csv('datasets/SIOE 2024-01-31-utf8.csv', encoding='utf-8', index=False)

In [3]:
print(df.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8797 entries, 0 to 8796
Data columns (total 49 columns):
 #   Column                                   Non-Null Count  Dtype 
---  ------                                   --------------  ----- 
 0   classe                                   8797 non-null   object
 1   tipo                                     8797 non-null   object
 2   código SIOE                              8797 non-null   int64 
 3   sigla                                    8797 non-null   object
 4   designação                               8797 non-null   object
 5   path                                     8797 non-null   object
 6   cae                                      8797 non-null   object
 7   sigla do ministério/secretaria regional  8797 non-null   object
 8   nome do ministério/secretaria regional   8797 non-null   object
 9   âmbito                                   8797 non-null   object
 10  endereço                                 8797 non-null   obj

In [1]:
import pandas as pd

df = pd.read_csv('datasets/SIOE 2024-01-31-utf8.csv', encoding='utf-8')

#nova coluna com o código postal em que extrai os primeiros 8 digitos do código postal original
df['codigo_postal'] = df['código postal'].str.extract(r'(\d{4}-\d{3})')

print(df.info())

#save the data to a new file csv file iso-8859-1
df.to_csv('datasets/SIOE 2024-01-31-utf8.csv', encoding='utf-8', index=False)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8797 entries, 0 to 8796
Data columns (total 52 columns):
 #   Column                                   Non-Null Count  Dtype  
---  ------                                   --------------  -----  
 0   classe                                   8797 non-null   object 
 1   tipo                                     8797 non-null   object 
 2   código SIOE                              8797 non-null   int64  
 3   sigla                                    8797 non-null   object 
 4   designação                               8797 non-null   object 
 5   path                                     8797 non-null   object 
 6   cae                                      8797 non-null   object 
 7   sigla do ministério/secretaria regional  8797 non-null   object 
 8   nome do ministério/secretaria regional   8797 non-null   object 
 9   âmbito                                   8797 non-null   object 
 10  endereço                                 8797 no

## ## latitude e longitude com CTT código postal API

In [11]:
import pandas as pd
import requests

# Suponho que já tens um DataFrame df com uma coluna 'codigo_postal'

# Atualiza a função fetch_lat_lon para a versão corrigida
def fetch_lat_lon(codigo_postal, api_key):
    if '-' in codigo_postal:
        try:
            cp4, cp3 = codigo_postal.split('-')
            url = f'https://www.cttcodigopostal.pt/api/v1/{api_key}/{cp4}-{cp3}'
            
            response = requests.get(url)
            if response.status_code == 200:  # Sucesso na resposta
                data = response.json()
                if data:  # Verifica se a lista de dados não está vazia
                    first_item = data[0]
                    if 'latitude' in first_item and 'longitude' in first_item:
                        return first_item['latitude'], first_item['longitude']
                    else:
                        return None, None
                else:
                    return None, None
            else:
                return None, None
        except Exception as e:
            print(f"Erro ao processar o código postal {codigo_postal}: {e}")
            return None, None
    else:
        return None, None

# Certifica-te de que a tua API-KEY está corretamente definida
api_key = 'bc10a7fe2f6744ab9719b0244d843d3b'

# Assegura que todos os códigos postais são tratados como strings
df['codigo_postal'] = df['codigo_postal'].astype(str)

# Aplica a função ao DataFrame e cria novas colunas para latitude e longitude
df[['latitude', 'longitude']] = pd.DataFrame(df['codigo_postal'].apply(lambda x: fetch_lat_lon(x, api_key)).tolist(), index=df.index)




In [10]:
def fetch_lat_lon(codigo_postal, api_key):
    if '-' in codigo_postal:
        try:
            cp4, cp3 = codigo_postal.split('-')
            url = f'https://www.cttcodigopostal.pt/api/v1/{api_key}/{cp4}-{cp3}'
            
            response = requests.get(url)
            if response.status_code == 200:  # Sucesso na resposta
                data = response.json()
                if data:  # Verifica se a lista de dados não está vazia
                    # Acessa o primeiro elemento da lista
                    first_item = data[0]
                    if 'latitude' in first_item and 'longitude' in first_item:
                        return first_item['latitude'], first_item['longitude']
                    else:
                        return None, None
                else:
                    return None, None
            else:
                return None, None
        except Exception as e:
            print(f"Erro ao processar o código postal {codigo_postal}: {e}")
            return None, None
    else:
        return None, None


# Agora, fazemos um teste com um código postal de exemplo
api_key = 'bc10a7fe2f6744ab9719b0244d843d3b' # Substitui pela tua API-KEY real
codigo_postal_teste = '1900-363' # Código postal de exemplo

# Fazemos a chamada à função com o código postal de teste
resultado_teste = fetch_lat_lon(codigo_postal_teste, api_key)
print(f"Resultado do teste: {resultado_teste}")


Resultado do teste: ('38.7254786', '-9.1170402')


In [ ]:
#save the data to a new file csv file iso-8859-1
df.to_csv('datasets/SIOE 2024-01-31-utf8.csv', encoding='utf-8', index=False)

## Latitude e longitude com Google maps

In [2]:
import pandas as pd

df = pd.read_csv('datasets/SIOE 2024-01-31-utf8.csv', encoding='utf-8')

In [8]:
import os
import googlemaps
from tqdm import tqdm


gmaps = googlemaps.Client(key=os.environ['GOOGLEMAPS_API_KEY'])


def extrair_lat_lng(codigo_postal):
    try:
        geocode_result = gmaps.geocode(codigo_postal)
        print(geocode_result)  # For debugging

        if len(geocode_result) > 0:  # Check if results are available
            location = geocode_result[0]['geometry']['location']
            return location['lat'], location['lng']
        else:
            # Handle cases where no results are found (e.g., return None)
            return None, None

    except Exception as e:
        print(f"Error processing: {e}")
        # Handle other potential exceptions (e.g., KeyError, TypeError)
        return None, None

# Rest of your code (assuming df is defined)...

latitudes = []
longitudes = []
for codigo_postal in tqdm(df['codigo_postal']):
    lat, lng = extrair_lat_lng(codigo_postal)
    latitudes.append(lat)
    longitudes.append(lng)

df['latitude'] = latitudes
df['longitude'] = longitudes

  0%|          | 4/8797 [00:00<15:33,  9.42it/s]

[]
[{'address_components': [{'long_name': '1250-068', 'short_name': '1250-068', 'types': ['postal_code']}, {'long_name': 'Lisbon', 'short_name': 'Lisbon', 'types': ['locality', 'political']}, {'long_name': 'Santo António', 'short_name': 'Santo António', 'types': ['administrative_area_level_3', 'political']}, {'long_name': 'Lisbon', 'short_name': 'Lisbon', 'types': ['administrative_area_level_2', 'political']}, {'long_name': 'Lisbon', 'short_name': 'Lisbon', 'types': ['administrative_area_level_1', 'political']}, {'long_name': 'Portugal', 'short_name': 'PT', 'types': ['country', 'political']}], 'formatted_address': '1250-068 Lisbon, Portugal', 'geometry': {'bounds': {'northeast': {'lat': 38.7250623, 'lng': -9.151523899999999}, 'southwest': {'lat': 38.7223629, 'lng': -9.1542209}}, 'location': {'lat': 38.7238987, 'lng': -9.1525448}, 'location_type': 'APPROXIMATE', 'viewport': {'northeast': {'lat': 38.7250623, 'lng': -9.151523419708496}, 'southwest': {'lat': 38.7223629, 'lng': -9.154221380

  0%|          | 7/8797 [00:00<12:25, 11.79it/s]

[]
[{'address_components': [{'long_name': '5370-347', 'short_name': '5370-347', 'types': ['postal_code']}, {'long_name': 'Mirandela', 'short_name': 'Mirandela', 'types': ['locality', 'political']}, {'long_name': 'Mirandela', 'short_name': 'Mirandela', 'types': ['administrative_area_level_3', 'political']}, {'long_name': 'Mirandela', 'short_name': 'Mirandela', 'types': ['administrative_area_level_2', 'political']}, {'long_name': 'Bragança District', 'short_name': 'Bragança District', 'types': ['administrative_area_level_1', 'political']}, {'long_name': 'Portugal', 'short_name': 'PT', 'types': ['country', 'political']}], 'formatted_address': '5370-347 Mirandela, Portugal', 'geometry': {'bounds': {'northeast': {'lat': 41.4908824, 'lng': -7.1763321}, 'southwest': {'lat': 41.4854013, 'lng': -7.184414}}, 'location': {'lat': 41.4871621, 'lng': -7.181721500000001}, 'location_type': 'APPROXIMATE', 'viewport': {'northeast': {'lat': 41.4908824, 'lng': -7.1763321}, 'southwest': {'lat': 41.4854013,

  0%|          | 13/8797 [00:00<08:50, 16.55it/s]

...

[{'address_components': [{'long_name': '8800-347', 'short_name': '8800-347', 'types': ['postal_code']}, {'long_name': 'Tavira', 'short_name': 'Tavira', 'types': ['locality', 'political']}, {'long_name': 'Santa Maria Tavira', 'short_name': 'Santa Maria Tavira', 'types': ['administrative_area_level_3', 'political']}, {'long_name': 'Tavira', 'short_name': 'Tavira', 'types': ['administrative_area_level_2', 'political']}, {'long_name': 'Faro District', 'short_name': 'Faro District', 'types': ['administrative_area_level_1', 'political']}, {'long_name': 'Portugal', 'short_name': 'PT', 'types': ['country', 'political']}], 'formatted_address': '8800-347 Tavira, Portugal', 'geometry': {'bounds': {'northeast': {'lat': 37.1267031, 'lng': -7.648029500000001}, 'southwest': {'lat': 37.1239504, 'lng': -7.6493858}}, 'location': {'lat': 37.1249545, 'lng': -7.6485414}, 'location_type': 'APPROXIMATE', 'viewport': {'northeast': {'lat': 37.1267031, 'lng': -7.647358669708498}, 'southwest': {'lat': 37.1239504

100%|█████████▉| 8793/8797 [11:19<00:00, 17.04it/s]

[]
[{'address_components': [{'long_name': '1600-226', 'short_name': '1600-226', 'types': ['postal_code']}, {'long_name': 'Lisbon', 'short_name': 'Lisbon', 'types': ['locality', 'political']}, {'long_name': 'São Domingos de Benfica', 'short_name': 'São Domingos de Benfica', 'types': ['administrative_area_level_3', 'political']}, {'long_name': 'Lisbon', 'short_name': 'Lisbon', 'types': ['administrative_area_level_2', 'political']}, {'long_name': 'Lisbon', 'short_name': 'Lisbon', 'types': ['administrative_area_level_1', 'political']}, {'long_name': 'Portugal', 'short_name': 'PT', 'types': ['country', 'political']}], 'formatted_address': '1600-226 Lisbon, Portugal', 'geometry': {'bounds': {'northeast': {'lat': 38.7548234, 'lng': -9.1719096}, 'southwest': {'lat': 38.7484765, 'lng': -9.174677899999999}}, 'location': {'lat': 38.7544715, 'lng': -9.173639699999999}, 'location_type': 'APPROXIMATE', 'viewport': {'northeast': {'lat': 38.7548234, 'lng': -9.1719096}, 'southwest': {'lat': 38.7484765,

100%|██████████| 8797/8797 [11:20<00:00, 12.93it/s]

[{'address_components': [{'long_name': '4150-081', 'short_name': '4150-081', 'types': ['postal_code']}, {'long_name': 'Porto', 'short_name': 'Porto', 'types': ['locality', 'political']}, {'long_name': 'Lordelo do Ouro', 'short_name': 'Lordelo do Ouro', 'types': ['administrative_area_level_3', 'political']}, {'long_name': 'Porto District', 'short_name': 'Porto District', 'types': ['administrative_area_level_2', 'political']}, {'long_name': 'Porto District', 'short_name': 'Porto District', 'types': ['administrative_area_level_1', 'political']}, {'long_name': 'Portugal', 'short_name': 'PT', 'types': ['country', 'political']}], 'formatted_address': '4150-081 Porto, Portugal', 'geometry': {'bounds': {'northeast': {'lat': 41.1568472, 'lng': -8.6408092}, 'southwest': {'lat': 41.15435, 'lng': -8.6435588}}, 'location': {'lat': 41.1552986, 'lng': -8.642022899999999}, 'location_type': 'APPROXIMATE', 'viewport': {'northeast': {'lat': 41.1569475802915, 'lng': -8.6408092}, 'southwest': {'lat': 41.15

## Preenchimento de valores em falta

In [10]:
#count missing values in the new columns
print(df['latitude'].isna().sum())
print(df['longitude'].isna().sum())

# import datasets\SIOE 2024-01-31-utf8 back.csv as dfCTT and count the number of missing values in the new columns
dfCTT = pd.read_csv('datasets\SIOE 2024-01-31-utf8 back.csv', encoding='utf-8')
print(dfCTT['latitude'].isna().sum())
print(dfCTT['longitude'].isna().sum())



2533
2533
852
852


In [20]:
#add the columns latitude and longitude of dfCTT in df and latitudeCTT and longitudeCTT
df['latitudeCTT'] = dfCTT['latitude']
df['longitudeCTT'] = dfCTT['longitude']



#count when both columns latitudeCTT and latitude have missing values
print(df[(df['latitudeCTT'].isna()) & (df['latitude'].isna())].shape[0])

#create a new column with the latitude and longitude of the CTT dataset with a condition the latitude is missing use the values of columns latitude and longitude  
df['latitudeFinal'] = df['latitudeCTT']
df['longitudeFinal'] = df['longitudeCTT']
df.loc[df['latitudeCTT'].isna(), 'latitudeFinal'] = df['latitude']
df.loc[df['latitudeCTT'].isna(), 'longitudeFinal'] = df['longitude']


530


In [21]:
#count missing values in the new columns
print(df['latitudeFinal'].isna().sum())
print(df['longitudeFinal'].isna().sum())

530
530


In [22]:
# Primeiro, ordena o DataFrame pelos códigos postais
df.sort_values(by='codigo_postal', inplace=True)

# Preenche os valores ausentes em 'latitudeFinal' e 'longitudeFinal'
# com o valor anterior (ou seguinte, se o anterior também for NaN)
df['latitudeFinal'] = df['latitudeFinal'].fillna(method='ffill').fillna(method='bfill')
df['longitudeFinal'] = df['longitudeFinal'].fillna(method='ffill').fillna(method='bfill')


C:\Users\Hugo\AppData\Local\Temp\ipykernel_3288\2722504293.py:6: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  df['latitudeFinal'] = df['latitudeFinal'].fillna(method='ffill').fillna(method='bfill')
C:\Users\Hugo\AppData\Local\Temp\ipykernel_3288\2722504293.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  df['longitudeFinal'] = df['longitudeFinal'].fillna(method='ffill').fillna(method='bfill')


In [19]:
#save the data to a new file csv file iso-8859-1
df.to_csv('datasets/SIOE 2024-01-31-utf8.csv', encoding='utf-8', index=False)

## Recoding de variáveis

In [3]:
df = pd.read_csv('datasets/SIOE 2024-01-31-utf8.csv', encoding='utf-8')

In [45]:
#mostras as modalidades da coluna tipo
print(df['tipo'].unique())

['CN+JUR' 'CN']


In [52]:
# criar coluna 'universo' em que se o valor da coluna tipo for igual a 'CN+JUR' fica Administração Pública Jurídica e se for CN fica Contas nacionais
df['universo'] = df['tipo'].apply(lambda x: 'Administração Pública Jurídica' if x == 'CN+JUR' else 'Contas nacionais')


In [57]:
# Usando expressão regular para extrair tudo antes do último "/"
df['dependencia'] = df['path'].str.extract(r'^([^/]+)')
df['dependencia'] = df['dependencia'].fillna('')
df['dependencia'] = df['dependencia'].astype(str)

# Inicializa a nova coluna 'dependencia_SIOE' com valores vazios
df['dependencia_SIOE'] = ''

# Cria um dicionário para mapear 'designação' para 'código SIOE'
designacao_to_sioe = pd.Series(df['código SIOE'].values, index=df['designação']).to_dict()

# Função para aplicar em cada linha
def find_dependencia_sioe(row):
    # Procura o 'código SIOE' correspondente à 'dependencia' na coluna 'designação'
    return designacao_to_sioe.get(row['dependencia'], '')

# Aplica a função a cada linha do DataFrame para preencher 'dependencia_SIOE'
df['dependencia_SIOE'] = df.apply(find_dependencia_sioe, axis=1)








In [58]:
# fazer nova coluna 'Codigo atividade economica'com os primeiros 5 digitos da coluna cae
df['Codigo atividade economica'] = df['cae'].str.extract(r'(\d{5})')

In [2]:
dfcontas = pd.read_csv('G:\database\contratos_18-23.csv', encoding='utf-8')


In [3]:
print(dfcontas.info())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 943144 entries, 0 to 943143
Data columns (total 12 columns):
 #   Column                     Non-Null Count   Dtype  
---  ------                     --------------   -----  
 0   idcontrato                 943144 non-null  int64  
 1   nAnuncio                   116961 non-null  object 
 2   tipoprocedimento           943144 non-null  object 
 3   objectoContrato            943016 non-null  object 
 4   dataPublicacao             943144 non-null  object 
 5   dataCelebracaoContrato     943144 non-null  object 
 6   precoContratual            943144 non-null  float64
 7   prazoExecucao              943144 non-null  int64  
 8   NIPC_entidade_comunicante  943144 non-null  int64  
 9   entidade_comunicante       943144 non-null  object 
 10  fundamentacao              933081 non-null  object 
 11  uuid                       943144 non-null  object 
dtypes: float64(1), int64(3), object(8)
memory usage: 86.3+ MB
None


In [8]:
#print(['NIPC_entidade_comunicante'].unique())

print(dfcontas['NIPC_entidade_comunicante'].nunique())

6811


In [11]:
df = pd.read_csv('datasets\SIOE 2024-01-31-utf8.csv', encoding='utf-8')

In [12]:
# Criar um dicionário a partir de dfcontas que mapeia entidade_comunicante para NIPC_entidade_comunicante
# Usamos drop_duplicates() para garantir que cada entidade_comunicante seja única antes de criar o dicionário
entidade_nipc_map = dfcontas.drop_duplicates(subset=['entidade_comunicante']).set_index('entidade_comunicante')['NIPC_entidade_comunicante'].to_dict()

# Usar o dicionário para mapear os NIPCs para df baseado em designação
df['NIPC'] = df['designação'].map(entidade_nipc_map)

print(df['NIPC'].isna().sum())

8242
